 # 1. Introduction and Defining Business Problem:

Berlin, It is a place where I am staying right now. In terms of population and area, Berlin is the largest city and capital for Germany. Berlin is the second famous startup hub in Europe.

## Problem Statement: Prospects for opening a food Restaurant or a new office in Berlin.

During the daytime, especially during lunch hours, office areas provide huge opportunities for restaurants.  An average meal priced (one lunch meal 5€). The shops are usually always full during lunch hours (11 am — 2-30 pm. Given this scenario, I will be showing the benefits and pitfalls of opening a restaurant in highly dense office places including office delivery. However, I am unaware of the profit, I do believe there will be huge benefits by opening a restaurant in the dense area of companies. I will be covering the top 10 places in Berlin.

Additionally, by understanding the type of companies that are located in each area will result in valuable information for opening a new office. Such as finding an area relatively less cost for opening an office and public transportation analysis to reach this company.

## Description of the data and solving the problems

To solve the above problems, a location-based dataset is important. However, neighther it is not available directly in internet nor from the Foursquare website. Hence, I decided to scrape the required data. 

There are 2 datasets:
    
    Company-related data with following columns:
        1. Company name: In Germany, a company is characterized as mbH, GmbH, AG, AG &Co.
        2. Address: It is composed of a street name, GPS coordinates, zip code, neighborhood
        3. Category: It is a type of company i.e software company, construction company e.t.c

    Berlin geographical dataset is composed with the following columns:
        1. Zip code
        2. Neighborhood
        3. District



### To solve above problems the following questions needed to answer.


    1. How many companies are located in each area? (i.e per zip code)
    2. Which type of shops are located near to each company? (i.e with the help GPS coordinates of a company). This particular question will be answered through Foursquare data.
    3. How similar each company in terms of its services?
    4. Possible public transportation services to reach the company?
    5. How far the residential area is located? 
    6. What are the average rental prices for a given area? By analyzing clusters of companys that are located for an area. (i.e This question will be answered if the data relevant data is available else will be skipped.)  


As a part of the report, I will walk you through each step of this project and address them separately. These answeres will justify a better place to open a restaurant or to open an office for my stakeholders. 

Let me, show you an outline of the initial data preparation. 



### Target Audience

#### What type of clients or a group of people would be interested in this project?

    1.For data scientists, who wnats to do exploratory data analysis techniques to obtain necessary data, analyze it, and, finally be able to tell a story out of it.
    2.Business personnel who wants to invest or open a restaurant. This analysis will be a comprehensive guide to start or expand restaurants targeting the large pool of office places during lunch hours.
    3. Furthermore, the analysis of company locations in Berlin will hugly benifit the business personnel for opening their new office.

# 2. Preprocessing the dataset  having companies list, postal codes and neighborhoods in Berlin

In [1]:
import wikipedia
from bs4 import BeautifulSoup
import pandas as pd
import numpy as np
import unicodedata
import requests
import json

### Extract Berlin neighborhoods and boroughs from wiki using BeautifulSoup

#### If like to scrape the data, run the following block of code.

```python
wiki_page = "https://de.wikipedia.org/wiki/Verwaltungsgliederung_Berlins"

html_ = requests.get(wiki_page)
soup = BeautifulSoup(html_.content, "html.parser")
table = soup.find_all("table")
data_table = table[2]

data_nei_ = []
columns = ["Nr","Ortteil","Bezirk","Flaeche","Einwohner_30_07_2019","Einwohner_km2"] 

for tr in data_table.find_all("tr")[1:]:
    data = []
    for td in tr.find_all("td"):
        data.append(td.get_text().strip())
    data_nei_.append(data)
data_nei_
df_nei = pd.DataFrame(data_nei_, columns=columns)
df_nei
```

### Step 2.1: Load dataset having district and its neighborhoods

In [2]:
berlin_neighborhoods = pd.read_csv("data/berlin_places.csv")
berlin_neighborhoods = berlin_neighborhoods[["Ortsteil","Bezirk"]]
berlin_neighborhoods["Ortsteil"] = berlin_neighborhoods["Ortsteil"].str.strip()
berlin_neighborhoods["Bezirk"] = berlin_neighborhoods["Bezirk"].str.strip()

### Step 2.2: Getting Coordinates of Major Districts(i.e Bezirk) : Geopy Client

##### if you like to get berlin district codes run the following code

```python
from geopy.geocoders import Nominatim
import json 
from geopy.exc import GeocoderTimedOut

geolocator = Nominatim(user_agent="a_explorer")

def explore(x):
    ll = geolocator.geocode(x)
    return (ll.latitude, ll.longitude)

def do_geocode(x):
    try:
        return explore(x)
    except GeocoderTimedOut:
        return explore(x)


unique_bezirk = berlin_neighborhoods.Bezirk.unique()
# unique_ortteil = berlin_neighborhoods.Ortsteil.unique()
# unique_ortteil = [i.strip() for i in unique_ortteil]

ll = {}
for item in unique_bezirk:
    x,y = do_geocode(item)
    ll[item] = (x,y)
ll
```

In [3]:
with open("data/bezirkgeo.json", "r") as f:
    geo_district = json.load(f)

berlin_neighborhoods["Bezirkgeo"] = berlin_neighborhoods.Bezirk.apply(lambda x: geo_district[x])
berlin_neighborhoods.head()

Ortsteil Bezirk                 Bezirkgeo
0         Mitte  Mitte  [52.5176896, 13.4023757]
1        Moabit  Mitte  [52.5176896, 13.4023757]
2  Hansaviertel  Mitte  [52.5176896, 13.4023757]
3    Tiergarten  Mitte  [52.5176896, 13.4023757]
4       Wedding  Mitte  [52.5176896, 13.4023757]

### Step 2.3: Load the daset having neighborhood and its postal codes

In [4]:
berlin_postalcodes = pd.read_excel("data/Bundesland Berlin.xlsx")
berlin_postalcodes[berlin_postalcodes.Ortsteil=="Wedding"]

PLZ Ortsteil
241  13347  Wedding
243  13349  Wedding
244  13351  Wedding
246  13353  Wedding
249  13357  Wedding
251  13359  Wedding
256  13405  Wedding
259  13407  Wedding
262  13409  Wedding

### Step 2.4: Load the dataset having company and its address, category of comapny, gps coordinates. 

In [5]:
profiles = pd.read_csv("data/company_profile.csv")
profiles = profiles[["url","location","info","branch"]]
profiles['location'] = profiles['location'].apply(lambda x: "{:.3f}".format(x) if not pd.isnull(x) else x)

In [6]:
# Grouping values based on company name, i.e a single row per company
profiles['location'] = profiles['location'].astype(str)
profiles['info'] = profiles['info'].astype(str)
cleaned_profiles = profiles.groupby(["url"])["info"].agg([('info', ','.join)])
cleaned_location = profiles.groupby(["url"])["location"].agg([('location', ','.join)])
profiles["branch"] = profiles["branch"].astype(str)
cleaned_branch = profiles.groupby(["url"])["branch"].agg([('branch', ','.join)])
cleaned_branch["branch"] = cleaned_branch["branch"].apply(lambda x : [x.split(",")[0]])
print(cleaned_branch.head())
print(cleaned_location.head())
print(cleaned_profiles.head())

                                                                                        branch
url                                                                                           
(KA) Kraft Automobile GmbH                          [Autohandel und Kfz-Handel (Nutzfahrzeuge]
(know:bodies) gesellschaft für integrierte komm...                 [Public-Relations-Beratung]
07schanksysteme gmbh                                        [Herstellung von Messinstrumenten]
0815-Industries KG                                                     [Werbung und Marketing]
1 Berlin x Hausverwaltung GmbH + Co. KG                                           [Verwaltung]
                                                                         location
url                                                                              
(KA) Kraft Automobile GmbH                          52.479,13.336,nan,nan,nan,nan
(know:bodies) gesellschaft für integrierte komm...  52.518,13.287,nan,nan,nan,nan
07schan

In [7]:
# Creating location dataframe from a list of values
cleaned_location["location"] = cleaned_location["location"].apply(lambda x : x.split(",")[:2])
cleaned_location = pd.DataFrame(cleaned_location["location"].values.tolist(), columns = ["Lat", "Lon"])
cleaned_location.head(8)

Lat     Lon
0  52.479  13.336
1  52.518  13.287
2  52.542  13.355
3  52.564  13.474
4     nan     nan
5     nan     nan
6     nan     nan
7  52.455  13.396

In [8]:
# Creating profile dataframe from a list of values
cleaned_profiles["info"] = cleaned_profiles["info"].apply(lambda x: x.split(",")[2:6])
cleaned_profiles = pd.DataFrame(cleaned_profiles["info"].values.tolist())
cleaned_profiles.columns= ["Name", "Street","Zipcode","City"]
cleaned_profiles.head(8)

Name  \
0                         (KA) Kraft Automobile GmbH   
1  (know:bodies) gesellschaft für integrierte kom...   
2                               07schanksysteme gmbh   
3                                 0815-Industries KG   
4                                              14195   
5                                              14195   
6                                              14195   
7                               1-2-3 Beschläge GmbH   

                          Street Zipcode    City  
0                  Wexstrasse 15   10715  Berlin  
1  Sophie-Charlotten-Strasse 103   14059  Berlin  
2             Sprengelstrasse 15   13353  Berlin  
3           Feldtmannstrasse 152   13088  Berlin  
4                         Berlin    None    None  
5                         Berlin    None    None  
6                         Berlin    None    None  
7              Colditzstrasse 33   12099  Berlin

In [9]:
# Creating branch dataframe from a list of values
cleaned_branch = pd.DataFrame(cleaned_branch["branch"].values.tolist(), columns=["Branch"])
cleaned_branch.head(8)

Branch
0           Autohandel und Kfz-Handel (Nutzfahrzeuge
1                          Public-Relations-Beratung
2                   Herstellung von Messinstrumenten
3                              Werbung und Marketing
4                                         Verwaltung
5    Vermögensberater und sonstige Vermögensberatung
6  Verwaltung und Management von Unternehmen und ...
7          Herstellung von Schlössern und Beschlägen

In [10]:
# Appending all columns together
company_data = pd.concat([cleaned_profiles,cleaned_location, cleaned_branch], axis=1)
print(company_data.shape)
company_data.head(8)

(6119, 7)


Name  \
0                         (KA) Kraft Automobile GmbH   
1  (know:bodies) gesellschaft für integrierte kom...   
2                               07schanksysteme gmbh   
3                                 0815-Industries KG   
4                                              14195   
5                                              14195   
6                                              14195   
7                               1-2-3 Beschläge GmbH   

                          Street Zipcode    City     Lat     Lon  \
0                  Wexstrasse 15   10715  Berlin  52.479  13.336   
1  Sophie-Charlotten-Strasse 103   14059  Berlin  52.518  13.287   
2             Sprengelstrasse 15   13353  Berlin  52.542  13.355   
3           Feldtmannstrasse 152   13088  Berlin  52.564  13.474   
4                         Berlin    None    None     nan     nan   
5                         Berlin    None    None     nan     nan   
6                         Berlin    None    None     nan     nan   
7              Colditzstrasse 33   12099  Berlin  52.455  13.396   

                                              Branch  
0           Autohandel und Kfz-Handel (Nutzfahrzeuge  
1                          Public-Relations-Beratung  
2                   Herstellung von Messinstrumenten  
3                              Werbung und Marketing  
4                                         Verwaltung  
5    Vermögensberater und sonstige Vermögensberatung  
6  Verwaltung und Management von Unternehmen und ...  
7          Herstellung von Schlössern und Beschlägen

In [11]:
# Droping data which does't have Latitude an longitude
company_data = company_data.dropna()
print(company_data.shape)
company_data.head(8)

(5660, 7)


Name  \
0                          (KA) Kraft Automobile GmbH   
1   (know:bodies) gesellschaft für integrierte kom...   
2                                07schanksysteme gmbh   
3                                  0815-Industries KG   
7                                1-2-3 Beschläge GmbH   
8                 1-2-3 Gebäudemanagement Berlin GmbH   
9              1-2-3 Marriage UG (haftungsbeschränkt)   
10                1. maXXwill UG (haftungsbeschränkt)   

                           Street Zipcode    City     Lat     Lon  \
0                   Wexstrasse 15   10715  Berlin  52.479  13.336   
1   Sophie-Charlotten-Strasse 103   14059  Berlin  52.518  13.287   
2              Sprengelstrasse 15   13353  Berlin  52.542  13.355   
3            Feldtmannstrasse 152   13088  Berlin  52.564  13.474   
7               Colditzstrasse 33   12099  Berlin  52.455  13.396   
8            Fredericiastrasse 28   14059  Berlin  52.511  13.282   
9             Elisabethstrasse 35   12307  Berlin  52.390  13.387   
10              Hubertusstrasse 8   12163  Berlin  52.460  13.326   

                                       Branch  
0    Autohandel und Kfz-Handel (Nutzfahrzeuge  
1                   Public-Relations-Beratung  
2            Herstellung von Messinstrumenten  
3                       Werbung und Marketing  
7   Herstellung von Schlössern und Beschlägen  
8                      Reinigung von Gebäuden  
9                     Dienstleistungen a.n.g.  
10                  Grosshandel mit Computern

In [12]:
# Check if there exist wrong entries in the dataset
outliers = company_data[company_data["City"] !="Berlin"]
company_data = company_data[company_data["City"] =="Berlin"]

In [13]:
# Selecting entries that having valid a street name and number
street_idx = outliers["Zipcode"].index
streets = outliers["Zipcode"].values.tolist()
idxes = []
for id_, street in enumerate(streets):
    if "strasse" in street.lower():
        idxes.append(street_idx[id_])
outliers = outliers.loc[idxes]

In [14]:
# Correcting entries that wrongly entered in the dataset
outliers["Name"] = outliers["Name"]+" "+outliers["Street"]
outliers["Street"] = outliers["Zipcode"]
outliers["Zipcode"] = outliers["City"]
outliers["City"] = "Berlin"
outliers

Name  \
213   ASIAGOURMET Asiatische Gastronomie  Service un...   
697   BPT Beratungs-  Planungs- und Treuhandgesellsc...   
715   BTB-Blockheizkraftwerk  Träger- + Betreiberges...   
921                     Blum und Partner  Rechtsanwälte   
931   Boeing Operations International  Inc. Zweignie...   
948    Borovac-Knabe und Partner  Trainer + Consultants   
1328           Cura Concept Management  Peter Rühl e.K.   
1450           DRESTATE Objekt Hamburg  Pinkertweg GmbH   
1652   Dr. Galwelat cimdata GmbH  Medienakademie Berlin   
1959  FBG eG  Firmen fördern nach biblischen Grundsä...   
2010                            FUTURELED GmbH Haus 201   
2155  Friedrich Scharf GmbH Garten-  Landschafts- + ...   
2514       Graf + Frey  Kultur- und Konzeptagentur GmbH   
2662  HMKW - Hochschule für Medien  Kommunikation un...   
2871  Holk  Kaletta Associates Gesellschaft Beratend...   
2932  Hygiea Dienstleistung GmbH  Glas- und Gebäuder...   
3041                 IPSER  Inter Personal Service e.K.   
3512                     Kryolan GmbH  Chemische Fabrik   
3546  Kühnel  Rosenmüller + Kollegen Rechtsanwälte P...   
3736  Lumen - Gesellschaft für Organisationsentwickl...   
3849            MME Me  Myself + Eye Entertainment GmbH   
4006  Merula Projektentwicklungs-  Baubetreuungs- un...   
4311  Onmarx  Online Marketing Agentur Berlin UG (ha...   
4332  Otto Kittel GmbH + Co. Garten-  Landschafts- u...   
4408  PROMOS consult Projektmanagement  Organisation...   
4409  PROMOS consult Projektmanagement  Organisation...   
5072                 Teller  Tisch + Tasse service GmbH   
5499     aust und partner - Steuerberater  Rechtsanwalt   
5571       cARE M + P - Capital  Art + Real Estate GmbH   
5998  plarewa Ingenieurgesellschaft für Planung  Rea...   
6015  raumpool Habich Krieger Töchterle-Knuth Partne...   

                          Street Zipcode    City     Lat     Lon  \
213         Meeraner Strasse 13c   12681  Berlin  52.528  13.524   
697      Französische Strasse 55   10117  Berlin  52.515  13.388   
715              Gaussstrasse 11   10589  Berlin  52.530  13.311   
921      Fehrbelliner Strasse 50   10119  Berlin  52.534  13.400   
931               Lennestrasse 9   10785  Berlin  52.512  13.375   
948             Knaackstrasse 88   10435  Berlin  52.540  13.415   
1328          Schwedenstrasse 14   13357  Berlin  52.555  13.376   
1450       Oudenarder Strasse 16   13347  Berlin  52.554  13.359   
1652        Windscheidstrasse 18   10627  Berlin  52.506  13.299   
1959       Haynauer Strasse 72 A   12249  Berlin  52.434  13.367   
2010      Köpenicker Strasse 325   12555  Berlin  52.385  13.522   
2155         Gatower Strasse 145   13595  Berlin  52.507  13.180   
2514           Mommsenstrasse 11   10629  Berlin  52.503  13.316   
2662             Ackerstrasse 76   13355  Berlin  52.539  13.384   
2871            Keithstrasse 2-4   10787  Berlin  52.502  13.346   
2932             Hauptstrasse 34   13127  Berlin  52.612  13.433   
3041       Kurfürstenstrasse 114   10787  Berlin  52.504  13.348   
3512            Papierstrasse 10   13409  Berlin  52.565  13.379   
3546        Berliner Strasse 117   10713  Berlin  52.487  13.317   
3736      Weydingerstrasse 14-16   10178  Berlin  52.527  13.413   
3849     Gotzkowskystrasse 20-21   10555  Berlin  52.523  13.329   
4006         Lübarser Strasse 2a   13435  Berlin  52.599  13.333   
4311           Ringbahnstrasse 7   10711  Berlin  52.499  13.289   
4332            Säntisstrasse 75   12277  Berlin  52.418  13.388   
4408             Rungestrasse 19   10179  Berlin  52.512  13.420   
4409             Rungestrasse 19   10179  Berlin  52.512  13.420   
5072           Elbestrasse 28/29   12045  Berlin  52.485  13.440   
5499              Markstrasse 45   13409  Berlin  52.563  13.365   
5571          Krausnickstrasse 1   10115  Berlin  52.524  13.396   
5998  Grossbeerenstrasse 169-171   12277  Berlin  52.429  13.376   
6015      Marienburger Strasse 8   10405  Berlin  52.5

In [15]:
# Appending data back to company dataset
company_data = company_data.append(outliers)
company_data = company_data.reset_index(drop=True)

In [16]:
company_data.head()

Name  \
0                         (KA) Kraft Automobile GmbH   
1  (know:bodies) gesellschaft für integrierte kom...   
2                               07schanksysteme gmbh   
3                                 0815-Industries KG   
4                               1-2-3 Beschläge GmbH   

                          Street Zipcode    City     Lat     Lon  \
0                  Wexstrasse 15   10715  Berlin  52.479  13.336   
1  Sophie-Charlotten-Strasse 103   14059  Berlin  52.518  13.287   
2             Sprengelstrasse 15   13353  Berlin  52.542  13.355   
3           Feldtmannstrasse 152   13088  Berlin  52.564  13.474   
4              Colditzstrasse 33   12099  Berlin  52.455  13.396   

                                      Branch  
0   Autohandel und Kfz-Handel (Nutzfahrzeuge  
1                  Public-Relations-Beratung  
2           Herstellung von Messinstrumenten  
3                      Werbung und Marketing  
4  Herstellung von Schlössern und Beschlägen

In [17]:
# Removing extra space around string 
unique_ortteil = berlin_neighborhoods.Ortsteil.unique()
unique_ortteil = [i.strip() for i in unique_ortteil]

### Step 2.5: Load the dataset having avarage rental price per Ortsteil

In [18]:
avgprice = pd.read_csv("data/prices.csv") 
# preprocess data 
avg1 = avgprice["text"][0]
avg1 = list(filter(None, [item.strip() for item in avg1.split("\n")]))

avg2 = avgprice["text"][1]
avg2 = list(filter(None, [item.strip() for item in avg2.split("\n")]))

In [19]:
def dataframe(x):
    y = np.array(x)
    y = y.reshape(-1,2)
    df = pd.DataFrame(y[1:], columns=y[0])
    df["Ortsteil"] = df["STADTTEIL"].apply(lambda x : x.split(" (")[0])
    return df

In [20]:
df_avg1 = dataframe(avg1)
df_avg1.head()

STADTTEIL     €/m²            Ortsteil
0  Lichterfelde (Steglitz)  11,20 €        Lichterfelde
1  Mahlsdorf (Hellersdorf)  10,36 €           Mahlsdorf
2   Mariendorf (Tempelhof)  10,90 €          Mariendorf
3  Marienfelde (Tempelhof)  19,82 €         Marienfelde
4       Märkisches Viertel   8,22 €  Märkisches Viertel

In [21]:
df_avg2 = dataframe(avg2)
df_avg2.head()

STADTTEIL     €/m²              Ortsteil
0                      Adlershof (Treptow)  12,51 €             Adlershof
1  Alt-Hohenschönhausen (Hohenschönhausen)  10,76 €  Alt-Hohenschönhausen
2                              Alt-Treptow  12,90 €           Alt-Treptow
3                   Altglienicke (Treptow)   9,95 €          Altglienicke
4                 Baumschulenweg (Treptow)  10,82 €        Baumschulenweg

In [22]:
Ortsteil_price = pd.concat([df_avg1, df_avg2]).reset_index(drop=True)
Ortsteil_price

STADTTEIL     €/m²            Ortsteil
0     Lichterfelde (Steglitz)  11,20 €        Lichterfelde
1     Mahlsdorf (Hellersdorf)  10,36 €           Mahlsdorf
2      Mariendorf (Tempelhof)  10,90 €          Mariendorf
3     Marienfelde (Tempelhof)  19,82 €         Marienfelde
4          Märkisches Viertel   8,22 €  Märkisches Viertel
..                        ...      ...                 ...
81        Köpenick (Köpenick)  11,62 €            Köpenick
82      Kreuzberg (Kreuzberg)  16,54 €           Kreuzberg
83        Lankwitz (Steglitz)  10,07 €            Lankwitz
84  Lichtenberg (Lichtenberg)  11,60 €         Lichtenberg
85    Lichtenrade (Tempelhof)   9,52 €         Lichtenrade

[86 rows x 3 columns]

### Step 2.6: Using Foursquare location data for each company location 

Preparing data for each company is a big deal. However, I woul like to skip this process just for time beeing. I will come back again to this step after having a good understanding of company data.

### Step 2.7: Combining all datasets except company dataset

In [23]:
Ortsteil_prices = Ortsteil_price[["Ortsteil","€/m²"]].set_index("Ortsteil")
dict_ortprice = Ortsteil_prices.to_dict()["€/m²"]

In [24]:
def insert_price(x):
    x = x.strip()
    if x in dict_ortprice.keys():
        x = dict_ortprice[x]
        x = x.split()[0]
        x = x.replace(",",".")
    else:
        x = 0
    return x

berlin_neighborhoods["€/m²"] = berlin_neighborhoods["Ortsteil"].apply(lambda x : insert_price(x))
berlin_neighborhoods["€/m²"] = berlin_neighborhoods["€/m²"].astype(float)
berlin_neighborhoods.head()

Ortsteil Bezirk                 Bezirkgeo   €/m²
0         Mitte  Mitte  [52.5176896, 13.4023757]  17.27
1        Moabit  Mitte  [52.5176896, 13.4023757]  17.59
2  Hansaviertel  Mitte  [52.5176896, 13.4023757]  16.55
3    Tiergarten  Mitte  [52.5176896, 13.4023757]  16.04
4       Wedding  Mitte  [52.5176896, 13.4023757]  11.33

In [25]:
berlin_postalcodes = berlin_postalcodes.set_index("Ortsteil")
berlin_neighborhoods = berlin_neighborhoods.set_index("Ortsteil")

In [26]:
merged = berlin_postalcodes.merge(berlin_neighborhoods, left_index=True, right_index=True)

In [27]:
merged

PLZ               Bezirk                 Bezirkgeo  \
Ortsteil                                                                     
Adlershof             12487     Treptow-Köpenick   [52.417893, 13.6001848]   
Adlershof             12489     Treptow-Köpenick   [52.417893, 13.6001848]   
Alt-Hohenschönhausen  13051          Lichtenberg    [52.534306, 13.502326]   
Alt-Hohenschönhausen  13053          Lichtenberg    [52.534306, 13.502326]   
Alt-Hohenschönhausen  13055          Lichtenberg    [52.534306, 13.502326]   
...                     ...                  ...                       ...   
Zehlendorf            14129  Steglitz-Zehlendorf  [52.4292052, 13.2299741]   
Zehlendorf            14163  Steglitz-Zehlendorf  [52.4292052, 13.2299741]   
Zehlendorf            14165  Steglitz-Zehlendorf  [52.4292052, 13.2299741]   
Zehlendorf            14167  Steglitz-Zehlendorf  [52.4292052, 13.2299741]   
Zehlendorf            14169  Steglitz-Zehlendorf  [52.4292052, 13.2299741]   

                       €/m²  
Ortsteil                     
Adlershof             12.51  
Adlershof             12.51  
Alt-Hohenschönhausen  10.76  
Alt-Hohenschönhausen  10.76  
Alt-Hohenschönhausen  10.76  
...                     ...  
Zehlendorf            11.89  
Zehlendorf            11.89  
Zehlendorf            11.89  
Zehlendorf            11.89  
Zehlendorf            11.89  

[355 rows x 4 columns]

### 2.7.1 Replacing zero values of rent with the mean values of corresponding district. 

In [28]:
print("Districts having no avarage rent values: ")
merged[merged["€/m²"]==0].Bezirk.unique().tolist()

Districts having no avarage rent values: 


['Pankow',
 'Charlottenburg-Wilmersdorf',
 'Lichtenberg',
 'Spandau',
 'Reinickendorf']

In [29]:
# evaluating mean values for zero rent values of district.
mean_lichtenberg = merged[(merged["Bezirk"]=='Lichtenberg') & (merged["€/m²"] !=0)]["€/m²"].mean()
mean_pankow = merged[(merged["Bezirk"]=='Pankow') & (merged["€/m²"] !=0)]["€/m²"].mean()
mean_charwil = merged[(merged["Bezirk"]=='Charlottenburg-Wilmersdorf') & (merged["€/m²"] !=0)]["€/m²"].mean()
mean_spandau = merged[(merged["Bezirk"]=='Spandau') & (merged["€/m²"] !=0)]["€/m²"].mean()
mean_reini = merged[(merged["Bezirk"]=='Reinickendorf') & (merged["€/m²"] !=0)]["€/m²"].mean()

In [30]:
merged[merged["Bezirk"]=='Spandau']

PLZ   Bezirk                Bezirkgeo   €/m²
Ortsteil                                                          
Falkenhagener Feld  13583  Spandau  [52.535788, 13.1977924]   0.00
Falkenhagener Feld  13585  Spandau  [52.535788, 13.1977924]   0.00
Falkenhagener Feld  13589  Spandau  [52.535788, 13.1977924]   0.00
Falkenhagener Feld  13591  Spandau  [52.535788, 13.1977924]   0.00
Gatow               14089  Spandau  [52.535788, 13.1977924]   0.00
Hakenfelde          13585  Spandau  [52.535788, 13.1977924]  12.37
Hakenfelde          13587  Spandau  [52.535788, 13.1977924]  12.37
Hakenfelde          13589  Spandau  [52.535788, 13.1977924]  12.37
Haselhorst          13599  Spandau  [52.535788, 13.1977924]   8.07
Kladow              14089  Spandau  [52.535788, 13.1977924]  11.45
Siemensstadt        13599  Spandau  [52.535788, 13.1977924]   9.39
Siemensstadt        13627  Spandau  [52.535788, 13.1977924]   9.39
Siemensstadt        13629  Spandau  [52.535788, 13.1977924]   9.39
Spandau             13581  Spandau  [52.535788, 13.1977924]   9.30
Spandau             13583  Spandau  [52.535788, 13.1977924]   9.30
Spandau             13585  Spandau  [52.535788, 13.1977924]   9.30
Spandau             13587  Spandau  [52.535788, 13.1977924]   9.30
Spandau             13597  Spandau  [52.535788, 13.1977924]   9.30
Spandau             14052  Spandau  [52.535788, 13.1977924]   9.30
Staaken             13581  Spandau  [52.535788, 13.1977924]  10.20
Staaken             13591  Spandau  [52.535788, 13.1977924]  10.20
Staaken             13593  Spandau  [52.535788, 13.1977924]  10.20
Wilhelmstadt        13581  Spandau  [52.535788, 13.1977924]   0.00
Wilhelmstadt        13593  Spandau  [52.535788, 13.1977924]   0.00
Wilhelmstadt        13595  Spandau  [52.535788, 13.1977924]   0.00
Wilhelmstadt        13597  Spandau  [52.535788, 13.1977924]   0.00

In [31]:
# Replacing zero values with the mean values.
merged.loc[(merged["Bezirk"]=='Pankow')&(merged["€/m²"]==0),"€/m²"]= mean_pankow
merged.loc[(merged["Bezirk"]=='Spandau')&(merged["€/m²"]==0),"€/m²"]= mean_spandau
merged[merged["Bezirk"]=='Spandau']

PLZ   Bezirk                Bezirkgeo       €/m²
Ortsteil                                                              
Falkenhagener Feld  13583  Spandau  [52.535788, 13.1977924]  10.070588
Falkenhagener Feld  13585  Spandau  [52.535788, 13.1977924]  10.070588
Falkenhagener Feld  13589  Spandau  [52.535788, 13.1977924]  10.070588
Falkenhagener Feld  13591  Spandau  [52.535788, 13.1977924]  10.070588
Gatow               14089  Spandau  [52.535788, 13.1977924]  10.070588
Hakenfelde          13585  Spandau  [52.535788, 13.1977924]  12.370000
Hakenfelde          13587  Spandau  [52.535788, 13.1977924]  12.370000
Hakenfelde          13589  Spandau  [52.535788, 13.1977924]  12.370000
Haselhorst          13599  Spandau  [52.535788, 13.1977924]   8.070000
Kladow              14089  Spandau  [52.535788, 13.1977924]  11.450000
Siemensstadt        13599  Spandau  [52.535788, 13.1977924]   9.390000
Siemensstadt        13627  Spandau  [52.535788, 13.1977924]   9.390000
Siemensstadt        13629  Spandau  [52.535788, 13.1977924]   9.390000
Spandau             13581  Spandau  [52.535788, 13.1977924]   9.300000
Spandau             13583  Spandau  [52.535788, 13.1977924]   9.300000
Spandau             13585  Spandau  [52.535788, 13.1977924]   9.300000
Spandau             13587  Spandau  [52.535788, 13.1977924]   9.300000
Spandau             13597  Spandau  [52.535788, 13.1977924]   9.300000
Spandau             14052  Spandau  [52.535788, 13.1977924]   9.300000
Staaken             13581  Spandau  [52.535788, 13.1977924]  10.200000
Staaken             13591  Spandau  [52.535788, 13.1977924]  10.200000
Staaken             13593  Spandau  [52.535788, 13.1977924]  10.200000
Wilhelmstadt        13581  Spandau  [52.535788, 13.1977924]  10.070588
Wilhelmstadt        13593  Spandau  [52.535788, 13.1977924]  10.070588
Wilhelmstadt        13595  Spandau  [52.535788, 13.1977924]  10.070588
Wilhelmstadt        13597  Spandau  [52.535788, 13.1977924]  10.070588

In [32]:
# Replacing zero values with the mean values.
merged.loc[(merged["Bezirk"]=='Lichtenberg')&(merged["€/m²"]==0),"€/m²"]= mean_lichtenberg
merged.loc[(merged["Bezirk"]=='Charlottenburg-Wilmersdorf')&(merged["€/m²"]==0),"€/m²"]= mean_charwil
merged.loc[(merged["Bezirk"]=='Reinickendorf')&(merged["€/m²"]==0),"€/m²"]= mean_reini
merged.head()

PLZ            Bezirk                Bezirkgeo   €/m²
Ortsteil                                                                     
Adlershof             12487  Treptow-Köpenick  [52.417893, 13.6001848]  12.51
Adlershof             12489  Treptow-Köpenick  [52.417893, 13.6001848]  12.51
Alt-Hohenschönhausen  13051       Lichtenberg   [52.534306, 13.502326]  10.76
Alt-Hohenschönhausen  13053       Lichtenberg   [52.534306, 13.502326]  10.76
Alt-Hohenschönhausen  13055       Lichtenberg   [52.534306, 13.502326]  10.76

In [33]:
merged.loc["Wedding"]

PLZ Bezirk                 Bezirkgeo   €/m²
Ortsteil                                               
Wedding   13347  Mitte  [52.5176896, 13.4023757]  11.33
Wedding   13349  Mitte  [52.5176896, 13.4023757]  11.33
Wedding   13351  Mitte  [52.5176896, 13.4023757]  11.33
Wedding   13353  Mitte  [52.5176896, 13.4023757]  11.33
Wedding   13357  Mitte  [52.5176896, 13.4023757]  11.33
Wedding   13359  Mitte  [52.5176896, 13.4023757]  11.33
Wedding   13405  Mitte  [52.5176896, 13.4023757]  11.33
Wedding   13407  Mitte  [52.5176896, 13.4023757]  11.33
Wedding   13409  Mitte  [52.5176896, 13.4023757]  11.33

# 3. Data visualization and exploration

In [34]:
# Explore companty data
print("Shape of the company data: ",company_data.shape)
company_data.columns.values

Shape of the company data:  (5616, 7)


array(['Name', 'Street', 'Zipcode', 'City', 'Lat', 'Lon', 'Branch'],
      dtype=object)

In [35]:
# find out how many company are located in each zip code
company_data["Zipcode"]= company_data["Zipcode"].astype(int)
def filter_location(x):
    if "." in x:
        x = x
    else:
        x = 0
    return x
company_data["Lat"] = company_data["Lat"].apply(lambda x : filter_location(x))
company_data["Lon"] = company_data["Lon"].apply(lambda x : filter_location(x))
company_data = company_data[(company_data["Lat"]!=0) &(company_data["Lon"] !=0)]

In [36]:
pincodes = berlin_postalcodes.reset_index().set_index("PLZ").to_dict()["Ortsteil"]

In [37]:
# assign Ortsteile to company data
def pincode(x):
    if x in pincodes.keys():
        x = pincodes[x]
    else:
        x = 0
    return x
    
company_data["Ortsteil"] = company_data["Zipcode"].apply(lambda x:pincode(x))

In [38]:
unknown_area = company_data[company_data["Ortsteil"]==0]
company_data = company_data[company_data["Ortsteil"]!=0]
company_data.shape


(5609, 8)

Empty DataFrame
Columns: [Name, Street, Zipcode, City, Lat, Lon, Branch, Ortsteil]
Index: []

### 3.1 Visulaize company location with help of Folium Library

In [40]:
import Count
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
import matplotlib.cm as cm
import matplotlib.colors as colors
import requests

# import k-means from clustering stage
from sklearn.cluster import KMeans
address = 'Berlin'

geolocator = Nominatim(user_agent="berlin_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Berlin are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Berlin are 52.5170365, 13.3888599.


#### 3.1.1 Create map of Berlin using latitude and longitude values

In [41]:

map_berlin = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, label in zip(company_data['Lat'], company_data['Lon'], company_data['Name']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_berlin)      
map_berlin

#### 3.1.2 Let's see the zipcode having above 50 companies

In [42]:
df_agg = company_data[['Ortsteil','Zipcode', 'Name']].groupby(['Ortsteil','Zipcode']).count()
df_agg = df_agg.reset_index()
df_agg = df_agg.sort_values(by = "Name", ascending=False)
df_agg_50 = df_agg[df_agg["Name"]>50]
print("Shape :", df_agg_50.shape)
df_agg_50

Shape : (27, 3)


Ortsteil  Zipcode  Name
93             Mitte    10117   516
180      Wilmersdorf    10719   187
94             Mitte    10178   164
92             Mitte    10115   149
16    Charlottenburg    10623   125
95             Mitte    10179   121
61         Kreuzberg    10785   120
120  Prenzlauer Berg    10119   109
177      Wilmersdorf    10707    93
121  Prenzlauer Berg    10405    86
64         Kreuzberg    10969    85
66         Kreuzberg    10999    76
65         Kreuzberg    10997    76
15    Charlottenburg    10587    76
46          Halensee    10709    72
42         Grunewald    10711    68
34    Friedrichshain    10245    65
142       Schöneberg    10787    65
88           Marzahn    12681    65
143       Schöneberg    10789    63
1          Adlershof    12489    63
19    Charlottenburg    10629    63
7        Borsigwalde    13509    59
33    Friedrichshain    10243    59
8              Britz    12099    55
85       Marienfelde    12277    53
63         Kreuzberg    10963    52

In [43]:
# Get zipcode cordinates for zipcodes having above 50 companies

import string
import random

zip50 = df_agg_50["Zipcode"].values.tolist()

In [44]:
def find_latlon(zipcodes):
    ll_array = {}
    N = 3
    try:
        while len(ll_array.keys()) != len(zipcodes):
            for zipcode in zipcodes:
                res = ''.join(random.choices(string.ascii_uppercase +string.digits, k = N))
                geolocator = Nominatim(user_agent="{}_explorer".format(res))
                print(res)
                ll = []
                location_ = geolocator.geocode(zipcode)
                latitude_ = location_.latitude
                longitude_ = location_.longitude
                ll.append(latitude_)
                ll.append(longitude_)
                print(ll)
                ll_array[zipcode]= ll
    except Exception as e:
        print(e)
    finally:
        return ll_array

In [45]:
ll_array = find_latlon(zip50)
ll_array

EW8
[52.5223502, 13.3957345]
036
[52.5031145, 13.331155]
HR5
[52.52027755, 13.4047296223029]
37V
[52.53195385, 13.3838001271759]
V20
[52.5076521, 13.3339024]
S99
[52.5119554914786, 13.4155794845406]
CLV
[52.5027367, 13.3519105]
MXV
[52.5301255, 13.4055081798411]
OSG
[52.4974608163396, 13.3139679031293]
OYM
[52.5395756, 13.4349415]
7OH
[52.5023686, 13.4022649715186]
MPZ
[52.498002901909, 13.4243136661234]
QQ8
[52.500838, 13.4397641163031]
CU1
[52.5174138, 13.3068805]
242
[52.49401945, 13.3030473222654]
LVX
[52.4984325, 13.2854946]
UQF
[52.5047255090411, 13.4620253636419]
OTM
[52.5044929954553, 13.346125454071]
O9T
Service not available


{10117: [52.5223502, 13.3957345],
 10719: [52.5031145, 13.331155],
 10178: [52.52027755, 13.4047296223029],
 10115: [52.53195385, 13.3838001271759],
 10623: [52.5076521, 13.3339024],
 10179: [52.5119554914786, 13.4155794845406],
 10785: [52.5027367, 13.3519105],
 10119: [52.5301255, 13.4055081798411],
 10707: [52.4974608163396, 13.3139679031293],
 10405: [52.5395756, 13.4349415],
 10969: [52.5023686, 13.4022649715186],
 10999: [52.498002901909, 13.4243136661234],
 10997: [52.500838, 13.4397641163031],
 10587: [52.5174138, 13.3068805],
 10709: [52.49401945, 13.3030473222654],
 10711: [52.4984325, 13.2854946],
 10245: [52.5047255090411, 13.4620253636419],
 10787: [52.5044929954553, 13.346125454071]}

In [49]:
last_seen = list(ll_array.keys())[-1]
new_zip = find_latlon(zip50[zip50.index(last_seen)+1:])

EJT
[52.4287101, 13.5451564]
30Z
[52.5028499076974, 13.309441005157]
222
[52.5914407205565, 13.2994196379183]
5K6
[52.5127617, 13.4264636]
82O
[52.461733502653, 13.3990879220802]
UNN
[52.41644311372, 13.3732390292676]
J88
[52.5003045261237, 13.3824990465792]


{12489: [52.4287101, 13.5451564],
 10629: [52.5028499076974, 13.309441005157],
 13509: [52.5914407205565, 13.2994196379183],
 10243: [52.5127617, 13.4264636],
 12099: [52.461733502653, 13.3990879220802],
 12277: [52.41644311372, 13.3732390292676],
 10963: [52.5003045261237, 13.3824990465792]}

In [50]:
# Update dictionaty of zip code lat and lon
ll_array.update(new_zip)
print(len(ll_array.keys()))

27


{10117: [52.5223502, 13.3957345],
 10719: [52.5031145, 13.331155],
 10178: [52.52027755, 13.4047296223029],
 10115: [52.53195385, 13.3838001271759],
 10623: [52.5076521, 13.3339024],
 10179: [52.5119554914786, 13.4155794845406],
 10785: [52.5027367, 13.3519105],
 10119: [52.5301255, 13.4055081798411],
 10707: [52.4974608163396, 13.3139679031293],
 10405: [52.5395756, 13.4349415],
 10969: [52.5023686, 13.4022649715186],
 10999: [52.498002901909, 13.4243136661234],
 10997: [52.500838, 13.4397641163031],
 10587: [52.5174138, 13.3068805],
 10709: [52.49401945, 13.3030473222654],
 10711: [52.4984325, 13.2854946],
 10245: [52.5047255090411, 13.4620253636419],
 10787: [52.5044929954553, 13.346125454071],
 12681: [52.5307082, 13.5223212],
 10789: [52.5021475, 13.3380110476059],
 12489: [52.4287101, 13.5451564],
 10629: [52.5028499076974, 13.309441005157],
 13509: [52.5914407205565, 13.2994196379183],
 10243: [52.5127617, 13.4264636],
 12099: [52.461733502653, 13.3990879220802],
 12277: [52.416

In [51]:
df_agg_50["ll"]= df_agg_50["Zipcode"].apply(lambda x : ll_array[x])

/home/prabhu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [52]:
df_50_loc = pd.DataFrame(df_agg_50["ll"].values.tolist(), columns=["Lat", "Lon"])
df_agg_50 = df_agg_50.reset_index(drop=True)
df_50_loc = pd.concat([df_agg_50,df_50_loc], axis =1)

Ortsteil  Zipcode  Count                                    ll  \
0             Mitte    10117    516              [52.5223502, 13.3957345]   
1       Wilmersdorf    10719    187               [52.5031145, 13.331155]   
2             Mitte    10178    164       [52.52027755, 13.4047296223029]   
3             Mitte    10115    149       [52.53195385, 13.3838001271759]   
4    Charlottenburg    10623    125              [52.5076521, 13.3339024]   
5             Mitte    10179    121  [52.5119554914786, 13.4155794845406]   
6         Kreuzberg    10785    120              [52.5027367, 13.3519105]   
7   Prenzlauer Berg    10119    109        [52.5301255, 13.4055081798411]   
8       Wilmersdorf    10707     93  [52.4974608163396, 13.3139679031293]   
9   Prenzlauer Berg    10405     86              [52.5395756, 13.4349415]   
10        Kreuzberg    10969     85        [52.5023686, 13.4022649715186]   
11        Kreuzberg    10999     76   [52.498002901909, 13.4243136661234]   
12        Kreuzberg    10997     76         [52.500838, 13.4397641163031]   
13   Charlottenburg    10587     76              [52.5174138, 13.3068805]   
14         Halensee    10709     72       [52.49401945, 13.3030473222654]   
15        Grunewald    10711     68              [52.4984325, 13.2854946]   
16   Friedrichshain    10245     65  [52.5047255090411, 13.4620253636419]   
17       Schöneberg    10787     65   [52.5044929954553, 13.346125454071]   
18          Marzahn    12681     65              [52.5307082, 13.5223212]   
19       Schöneberg    10789     63        [52.5021475, 13.3380110476059]   
20        Adlershof    12489     63              [52.4287101, 13.5451564]   
21   Charlottenburg    10629     63   [52.5028499076974, 13.309441005157]   
22      Borsigwalde    13509     59  [52.5914407205565, 13.2994196379183]   
23   Friedrichshain    10243     59              [52.5127617, 13.4264636]   
24            Britz    12099     55   [52.461733502653, 13.3990879220802]   
25      Marienfelde    12277     53    [52.41644311372, 13.3732390292676]   
26        Kreuzberg    10963     52  [52.5003045261237, 13.3824990465792]   

          Lat        Lon  
0   52.522350  13.395734  
1   52.503115  13.331155  
2   52.520278  13.404730  
3   52.531954  13.383800  
4   52.507652  13.333902  
5   52.511955  13.415579  
6   52.502737  13.351911  
7   52.530125  13.405508  
8   52.497461  13.313968  
9   52.539576  13.434942  
10  52.502369  13.402265  
11  52.498003  13.424314  
12  52.500838  13.439764  
13  52.517414  13.306881  
14  52.494019  13.303047  
15  52.498432  13.285495  
16  52.504726  13.462025  
17  52.504493  13.346125  
18  52.530708  13.522321  
19  52.502147  13.338011  
20  52.428710  13.545156  
21  52.502850  13.309441  
22  52.591441  13.299420  
23  52.512762  13.426464  
24  52.461734  13.399088  
25  52.416443  13.373239  
26  52.500305  13.382499

# 4. Evaluations

### 4.1. How many companies are located in each area? (i.e per zip code)

In [57]:
df_50_loc = df_50_loc.rename(columns={"Name":"Count"})
df_50_loc

Ortsteil  Zipcode  Count                                    ll  \
0             Mitte    10117    516              [52.5223502, 13.3957345]   
1       Wilmersdorf    10719    187               [52.5031145, 13.331155]   
2             Mitte    10178    164       [52.52027755, 13.4047296223029]   
3             Mitte    10115    149       [52.53195385, 13.3838001271759]   
4    Charlottenburg    10623    125              [52.5076521, 13.3339024]   
5             Mitte    10179    121  [52.5119554914786, 13.4155794845406]   
6         Kreuzberg    10785    120              [52.5027367, 13.3519105]   
7   Prenzlauer Berg    10119    109        [52.5301255, 13.4055081798411]   
8       Wilmersdorf    10707     93  [52.4974608163396, 13.3139679031293]   
9   Prenzlauer Berg    10405     86              [52.5395756, 13.4349415]   
10        Kreuzberg    10969     85        [52.5023686, 13.4022649715186]   
11        Kreuzberg    10999     76   [52.498002901909, 13.4243136661234]   
12        Kreuzberg    10997     76         [52.500838, 13.4397641163031]   
13   Charlottenburg    10587     76              [52.5174138, 13.3068805]   
14         Halensee    10709     72       [52.49401945, 13.3030473222654]   
15        Grunewald    10711     68              [52.4984325, 13.2854946]   
16   Friedrichshain    10245     65  [52.5047255090411, 13.4620253636419]   
17       Schöneberg    10787     65   [52.5044929954553, 13.346125454071]   
18          Marzahn    12681     65              [52.5307082, 13.5223212]   
19       Schöneberg    10789     63        [52.5021475, 13.3380110476059]   
20        Adlershof    12489     63              [52.4287101, 13.5451564]   
21   Charlottenburg    10629     63   [52.5028499076974, 13.309441005157]   
22      Borsigwalde    13509     59  [52.5914407205565, 13.2994196379183]   
23   Friedrichshain    10243     59              [52.5127617, 13.4264636]   
24            Britz    12099     55   [52.461733502653, 13.3990879220802]   
25      Marienfelde    12277     53    [52.41644311372, 13.3732390292676]   
26        Kreuzberg    10963     52  [52.5003045261237, 13.3824990465792]   

          Lat        Lon  
0   52.522350  13.395734  
1   52.503115  13.331155  
2   52.520278  13.404730  
3   52.531954  13.383800  
4   52.507652  13.333902  
5   52.511955  13.415579  
6   52.502737  13.351911  
7   52.530125  13.405508  
8   52.497461  13.313968  
9   52.539576  13.434942  
10  52.502369  13.402265  
11  52.498003  13.424314  
12  52.500838  13.439764  
13  52.517414  13.306881  
14  52.494019  13.303047  
15  52.498432  13.285495  
16  52.504726  13.462025  
17  52.504493  13.346125  
18  52.530708  13.522321  
19  52.502147  13.338011  
20  52.428710  13.545156  
21  52.502850  13.309441  
22  52.591441  13.299420  
23  52.512762  13.426464  
24  52.461734  13.399088  
25  52.416443  13.373239  
26  52.500305  13.382499

### 4.1.1 How many companies are located in each area? (i.e Ortsteil)

In [64]:
grouped = df_50_loc.groupby('Ortsteil')["Count"].sum().reset_index()
grouped.sort_values('Count', ascending=False)

Ortsteil  Count
10            Mitte    950
7         Kreuzberg    409
13      Wilmersdorf    280
3    Charlottenburg    264
11  Prenzlauer Berg    195
12       Schöneberg    128
4    Friedrichshain    124
6          Halensee     72
5         Grunewald     68
9           Marzahn     65
0         Adlershof     63
1       Borsigwalde     59
2             Britz     55
8       Marienfelde     53

After having data analysis of company data, it describes, neighborhood "Mitte" has the highest number of companies. "Kreuzberg" has the second-highest number of companies. However, "Schöneberg" and "Friedrichshain" are in the top 7 positions. "Mitte" area is situated in central Berlin and mostly in its old town, it is traversed by the river Spree. Also, most of the city tourist attractions are situated in Mitte. Hence, it does sound like an ideal location for having a restaurant or an office there. However, it might expensive. Let's continue with the further analysis of average rental prices and which types of venues have existed in each neighborhood. 

### 4.1.2 Let's start with the Mitte location, by analysing avarage rental price and type of company's

In [69]:
mitte_cd = company_data[company_data["Ortsteil"]=='Mitte']
mitte_cd.head()

Name                   Street  \
18  213 Gesellschaft für Besseres Wohnen mbH        Sophienstrasse 18   
24                              300plus GmbH       Rungestrasse 22-24   
37           4QD - Qualitätskliniken.de GmbH      Friedrichstrasse 60   
48            7flies UG (haftungsbeschränkt)  Französische Strasse 24   
49                       8KU Renewables GmbH        Schumannstrasse 2   

    Zipcode    City     Lat     Lon                                Branch  \
18    10178  Berlin  52.526  13.401               Dienstleistungen a.n.g.   
24    10179  Berlin  52.512  13.419                 Werbung und Marketing   
37    10117  Berlin  52.511  13.390     Webdesign und IT-Dienstleistungen   
48    10117  Berlin  52.515  13.391  Handelsvermittlung von Heimtextilien   
49    10117  Berlin  52.523  13.379                Elektrizitätserzeugung   

   Ortsteil  
18    Mitte  
24    Mitte  
37    Mitte  
48    Mitte  
49    Mitte

In [73]:
# Avarage rental price in Mitte
price_mitte = merged.loc["Mitte"]["€/m²"].mean()
price_mitte

17.27

In [ ]:
grouped.Ortsteil.values.to